# Exponential smoothing in SQL

In [ ]:
from pandas import DataFrame
import matplotlib.pyplot as plt
from data201 import db_connection, df_query

%matplotlib inline

In [ ]:
conn = db_connection(config_file='stock-prices.ini')

In [ ]:
def compute_exponential_smoothings(conn, alpha, label):
    """
    @conn the database connection
    @alpha the alpha value for exponential smoothing
    @label label for the exponentially smoothed values
    """
    conn.cursor().execute('SET @smoothed = NULL')
    
    return df_query(conn,
       f""" 
        SELECT days_ago, price,
               @smoothed := ({alpha}*price
                          + (1-{alpha})*(IF (@smoothed IS NULL, price, @smoothed)))
                   AS '{label}'
        FROM recent_prices
        ORDER BY days_ago
        """
    )

In [ ]:
plt.figure(figsize=(15, 10))

first = True

for a in [5, 2]:
    alpha = a/10
    graph_label = f'{alpha = }'
    
    df = compute_exponential_smoothings(conn, alpha, graph_label)
    display(df)

    rows = df.values.tolist()
    xs   = [row[0] for row in rows]
    ys   = [row[1] for row in rows]
    exps = [row[2] for row in rows]
    
    # Initialize the graph.
    if first:
        plt.xticks(xs)
        plt.plot(xs, ys, linewidth=5)
        plt.title('Exponentially Smoothed Stock Prices')
        plt.xlabel('Days ago')
        plt.ylabel('Price')
        first = False

    # Plot the moving average line.
    plt.plot(xs, exps, label=graph_label)
    
plt.legend()
plt.show()

In [ ]:
conn.close()